In [22]:
#Process World Factbook links to each country page
import requests
from bs4 import BeautifulSoup

countryurl = 'https://www.cia.gov/the-world-factbook/references/country-data-codes/'

response = requests.get(countryurl)
html_content = response.content
print(html_content)

string_data = html_content.decode('utf-8')
print(string_data.split('href'))


countrylinks = []
process = ''
for links in string_data.split('href'):
  if 'the-world-factbook/countries/' in links:
    process = links[len('the-world-factbook/countries/')+3:]
    print(process[:process.index('/')])
    countrylinks.append(process[:process.index('/')])

#print(countrylinks)

masterurl = 'https://www.cia.gov/the-world-factbook/countries/'

factbookcountrylinks = []
for links in countrylinks:
  print(masterurl + links + '/')
  factbookcountrylinks.append(masterurl + links + '/')

factbookcountrylinks = factbookcountrylinks[1:]

# Interestingly, as of 06/17/2023, there is currently not a working link for Cote d'Ivoire on
# https://www.cia.gov/the-world-factbook/countries/, so shown below is the link that is also added
cotedivoirelink = 'https://www.cia.gov/the-world-factbook/countries/cote-divoire/'
factbookcountrylinks.append(cotedivoirelink)

print(factbookcountrylinks)

b'<!DOCTYPE html><html lang="en"><head><meta charSet="utf-8"/><meta http-equiv="x-ua-compatible" content="ie=edge"/><meta name="viewport" content="width=device-width, initial-scale=1, shrink-to-fit=no"/><style id="typography.js">html{font-family:sans-serif;-ms-text-size-adjust:100%;-webkit-text-size-adjust:100%}body{margin:0}article,aside,details,figcaption,figure,footer,header,main,menu,nav,section,summary{display:block}audio,canvas,progress,video{display:inline-block}audio:not([controls]){display:none;height:0}progress{vertical-align:baseline}[hidden],template{display:none}a{background-color:transparent;}a:active,a:hover{outline-width:0}abbr[title]{border-bottom:none;text-decoration:underline;text-decoration:underline dotted}b,strong{font-weight:inherit;font-weight:bolder}dfn{font-style:italic}h1{font-size:2em;margin:.67em 0}mark{background-color:#ff0;color:#000}small{font-size:80%}sub,sup{font-size:75%;line-height:0;position:relative;vertical-align:baseline}sub{bottom:-.25em}sup{top

In [23]:
%%time
import requests
import re
import pandas as pd
from bs4 import BeautifulSoup
print(factbookcountrylinks)

#Initializes an empty dataframe
rawdataframe = pd.DataFrame()

# Loops through every url link for each entry in the CIA World Factbook, scrapes from each HTML,
# and consolidates all of it into a single pandas dataframe
for country in factbookcountrylinks:
  print(country)
  print(country.split('/')[-2])
  countriesname = country.split('/')[-2]
  # Send an HTTP GET request and retrieve the HTML content
  response = requests.get(country)
  html_content = response.content

  # Create a BeautifulSoup object
  soup = BeautifulSoup(html_content, 'html.parser')

  # Find all headings and paragraphs
  headings = soup.find_all(['h1', 'h2', 'h3', 'h4', 'h5', 'h6'])
  paragraphs = soup.find_all('p')

  # Create a mapping of heading to paragraph
  heading_paragraph_map = {}

  # Iterate over headings
  for heading in headings:
      # Find the next paragraph sibling for each heading
      next_paragraph = heading.find_next_sibling('p')
      if next_paragraph:
          # Store the heading as the key and the paragraph text as the value
          heading_paragraph_map[heading.text.strip()] = next_paragraph.text.strip()

  #Processes html headings and paragraphs into pandas dataframe with country names
  columns = ['name']
  rows = [countriesname]
  #Print the heading and corresponding paragraph
  for heading, paragraph in heading_paragraph_map.items():
      #print('Heading:', heading)
      #print('Paragraph:', paragraph)
      columns.append(heading)
      rows.append(paragraph)
      #print()
  print(columns)
  #print(rows)
  print(heading_paragraph_map.items())
  rawcountries = pd.DataFrame([rows], columns = columns)

  #Consolidates each country dataframe into a single raw dataframe
  rawdataframe = pd.concat([rawcountries, rawdataframe], sort=False)

print(rawdataframe)
rawdataframe.to_csv('rawCIAdata.csv', index = False)

['https://www.cia.gov/the-world-factbook/countries/afghanistan/', 'https://www.cia.gov/the-world-factbook/countries/akrotiri/', 'https://www.cia.gov/the-world-factbook/countries/albania/', 'https://www.cia.gov/the-world-factbook/countries/algeria/', 'https://www.cia.gov/the-world-factbook/countries/american-samoa/', 'https://www.cia.gov/the-world-factbook/countries/andorra/', 'https://www.cia.gov/the-world-factbook/countries/angola/', 'https://www.cia.gov/the-world-factbook/countries/anguilla/', 'https://www.cia.gov/the-world-factbook/countries/antarctica/', 'https://www.cia.gov/the-world-factbook/countries/antigua-and-barbuda/', 'https://www.cia.gov/the-world-factbook/countries/argentina/', 'https://www.cia.gov/the-world-factbook/countries/armenia/', 'https://www.cia.gov/the-world-factbook/countries/aruba/', 'https://www.cia.gov/the-world-factbook/countries/ashmore-and-cartier-islands/', 'https://www.cia.gov/the-world-factbook/countries/australia/', 'https://www.cia.gov/the-world-fact

In [28]:
%%time
import numpy as np
#Implements cleaning and preprocessing of data for several dataframe columns of interest,
# with the implementations for each column of interest shown below:
cleaneddata = rawdataframe[rawdataframe['name']!='world']
cleaneddata = cleaneddata[cleaneddata['name']!='french-southern-and-antarctic-lands']
cleaneddata.reset_index(inplace = True)

# Cleaning / Preprocessing for Urbanization Data
cleaneddata['Urbanization Rate (%)'] = cleaneddata['Urbanization'].str.replace('^urban+.*urbanization: ','', regex = True)
cleaneddata['Urbanization Rate (%)'] = cleaneddata['Urbanization Rate (%)'].str.split().str[0].str.replace('%','')
cleaneddata['Urbanization Rate (%)'] = cleaneddata['Urbanization Rate (%)'].fillna('0')
cleaneddata['Urbanization Rate (%)'] = cleaneddata['Urbanization Rate (%)'].str.replace('[A-Za-z]','0',regex = True)
cleaneddata['Urbanization Rate (%)'] = cleaneddata['Urbanization Rate (%)'].astype('float')

cleaneddata = cleaneddata.rename(columns={'Urbanization':'Urbanization (%)'})
cleaneddata['Urbanization (%)'] = cleaneddata['Urbanization (%)'].str.split().str[2]
cleaneddata['Urbanization (%)'] = cleaneddata['Urbanization (%)'].str.replace('%','')
cleaneddata['Urbanization (%)'] = cleaneddata['Urbanization (%)'].str.replace('[^0-9\.]','0',regex = True)
cleaneddata['Urbanization (%)'] = cleaneddata['Urbanization (%)'].fillna('0')
cleaneddata['Urbanization (%)'] = cleaneddata['Urbanization (%)'].astype('float')



# Cleaning / Preprocessing for Population Growth Rate Data
cleaneddata = cleaneddata.rename(columns={'Population growth rate':'Population growth rate (%)'})

cleaneddata['Population growth rate (%)'] = cleaneddata['Population growth rate (%)'].str.split().str[0]
cleaneddata['Population growth rate (%)'] = cleaneddata['Population growth rate (%)'].str.replace('%','')
cleaneddata['Population growth rate (%)'] = cleaneddata['Population growth rate (%)'].str.replace('[A-Za-z]','0', regex = True)
cleaneddata['Population growth rate (%)'] = cleaneddata['Population growth rate (%)'].fillna('0')
cleaneddata['Population growth rate (%)'] = cleaneddata['Population growth rate (%)'].astype('float')

# Cleaning / Preprocessing for Area Data
cleaneddata = cleaneddata.rename(columns={'Area':'Area_(sq/km)'})
cleaneddata['Area_(sq/km)'] = cleaneddata['Area_(sq/km)'].fillna('0')
cleaneddata['Area_(sq/km)'] = cleaneddata['Area_(sq/km)'].str.split('sq km').str[0]
cleaneddata['Area_(sq/km)'] = cleaneddata['Area_(sq/km)'].str.replace('total: ', '')
cleaneddata['Area_(sq/km)'] = cleaneddata['Area_(sq/km)'].str.replace('million', '000')
cleaneddata['Area_(sq/km)'] = cleaneddata['Area_(sq/km)'].str.replace('14.2', '14.200')
cleaneddata['Area_(sq/km)'] = cleaneddata['Area_(sq/km)'].str.replace(',', '')
cleaneddata['Area_(sq/km)'] = cleaneddata['Area_(sq/km)'].str.replace(' ', '')
cleaneddata['Area_(sq/km)'] = cleaneddata['Area_(sq/km)'].str.replace('.', '')
cleaneddata['Area_(sq/km)'] = cleaneddata['Area_(sq/km)'].astype('int64')

# Cleaning / Preprocessing for Coastline Data
cleaneddata = cleaneddata.rename(columns={'Coastline':'Coastline_(km)'})
cleaneddata['Coastline_(km)'] = cleaneddata['Coastline_(km)'].str.split(' ').str[0]
cleaneddata['Coastline_(km)'] = cleaneddata['Coastline_(km)'].fillna('0')
cleaneddata['Coastline_(km)'] = cleaneddata['Coastline_(km)'].str.replace(',','')
cleaneddata['Coastline_(km)'] = cleaneddata['Coastline_(km)'].str.replace('Saint','394')
cleaneddata['Coastline_(km)'] = cleaneddata['Coastline_(km)'].astype('float')

# Cleaning / Preprocessing for Agricultural Land Use Data
cleaneddata = cleaneddata.rename(columns={'Land use':'Agricultural Land Use (%)'})

cleaneddata['Agricultural Land Use (%)'] = cleaneddata['Agricultural Land Use (%)'].str.split('%').str[0]
cleaneddata['Agricultural Land Use (%)'] = cleaneddata['Agricultural Land Use (%)'].str.split('agricultural land: ').str[1]
cleaneddata['Agricultural Land Use (%)'] = cleaneddata['Agricultural Land Use (%)'].fillna('0')
cleaneddata['Agricultural Land Use (%)'] = cleaneddata['Agricultural Land Use (%)'].astype('float')

# Cleaning / Preprocessing for Irrigated Land Data
cleaneddata = cleaneddata.rename(columns={'Irrigated land':'Irrigated land (sq km)'})

cleaneddata['Irrigated land (sq km)'] = cleaneddata['Irrigated land (sq km)'].str.replace('''2013''','')
cleaneddata['Irrigated land (sq km)'] = cleaneddata['Irrigated land (sq km)'].str.replace('''[()]''','')
cleaneddata['Irrigated land (sq km)'] = cleaneddata['Irrigated land (sq km)'].str.split('sq km').str[0]
cleaneddata['Irrigated land (sq km)'] = cleaneddata['Irrigated land (sq km)'].str.replace(',','')
cleaneddata['Irrigated land (sq km)'] = cleaneddata['Irrigated land (sq km)'].fillna('0')
cleaneddata['Irrigated land (sq km)'] = cleaneddata['Irrigated land (sq km)'].str.replace('''NA''','0')
cleaneddata['Irrigated land (sq km)'] = cleaneddata['Irrigated land (sq km)'].astype('float')

# Cleaning / Preprocessing for Population Data
cleaneddata['Population'] = cleaneddata['Population'].fillna('0')
cleaneddata['Population'] = cleaneddata['Population'].str.replace('\(2020\) approximately ', '', regex = True)
cleaneddata['Population'] = cleaneddata['Population'].str.replace('approximately ','')
cleaneddata['Population'] = cleaneddata['Population'].str.split(' ').str[0]
cleaneddata['Population'] = cleaneddata['Population'].str.replace('uninhabited','0')
cleaneddata['Population'] = cleaneddata['Population'].str.replace('no','0')
cleaneddata['Population'] = cleaneddata['Population'].str.replace(';','')
cleaneddata['Population'] = cleaneddata['Population'].str.replace('\(July','0')
cleaneddata['Population'] = cleaneddata['Population'].str.replace('\(2018','0')
cleaneddata['Population'] = cleaneddata['Population'].str.replace(',','')
cleaneddata['Population'] = cleaneddata['Population'].astype('float')

# Cleaning / Preprocessing for Median Age Data
cleaneddata['Median age'] = cleaneddata['Median age'].str.split('years').str[0]
cleaneddata['Median age'] = cleaneddata['Median age'].str.replace('total: ','')
cleaneddata['Median age'] = cleaneddata['Median age'].fillna('0')
cleaneddata['Median age'] = cleaneddata['Median age'].astype('float')

# Cleaning / Preprocessing for Birth Rate Data
cleaneddata['Birth rate'] = cleaneddata['Birth rate'].str.split(' ').str[0]
cleaneddata['Birth rate'] = cleaneddata['Birth rate'].fillna('0')
cleaneddata['Birth rate'] = cleaneddata['Birth rate'].str.replace('[A-Za-z]','0', regex = True)
cleaneddata['Birth rate'] = cleaneddata['Birth rate'].astype('float')/1000

# Cleaning / Preprocessing for Death Rate Data
cleaneddata['Death rate'] = cleaneddata['Death rate'].str.replace('\(\d\d\d\d','0', regex = True)
cleaneddata['Death rate'] = cleaneddata['Death rate'].str.split(' ').str[0]
cleaneddata['Death rate'] = cleaneddata['Death rate'].fillna('0')
cleaneddata['Death rate'] = cleaneddata['Death rate'].str.replace('[A-Za-z]','0', regex = True)
cleaneddata['Death rate'] = cleaneddata['Death rate'].astype('float')/1000


# Cleaning / Preprocessing for Net Migration Rate Data
cleaneddata['Net migration rate'] = cleaneddata['Net migration rate'].str.split().str[0]
cleaneddata['Net migration rate'] = cleaneddata['Net migration rate'].fillna('0')
cleaneddata['Net migration rate'] = cleaneddata['Net migration rate'].str.replace('[A-Za-z]','0', regex = True)
cleaneddata['Net migration rate'] = cleaneddata['Net migration rate'].astype('float')/1000

# Cleaning / Preprocessing for Sex Ratio Data
cleaneddata=cleaneddata.rename(columns = {'Sex ratio' : 'Sex Ratio (male/female)'})
cleaneddata['Sex Ratio (male/female)'] = cleaneddata['Sex Ratio (male/female)'].str.replace('^.*total ','',regex = True)
cleaneddata['Sex Ratio (male/female)'] = cleaneddata['Sex Ratio (male/female)'].str.replace('[A-Za-z\:]','',regex = True)
cleaneddata['Sex Ratio (male/female)'] = cleaneddata['Sex Ratio (male/female)'].str.split().str[0]
cleaneddata['Sex Ratio (male/female)'] = cleaneddata['Sex Ratio (male/female)'].fillna('0')
cleaneddata['Sex Ratio (male/female)'] = cleaneddata['Sex Ratio (male/female)'].astype('float')

# Cleaning / Preprocessing for Mother's Age Data
cleaneddata['''Mother's mean age at first birth'''] = cleaneddata['''Mother's mean age at first birth'''].str.split().str[0]
cleaneddata['''Mother's mean age at first birth'''] = cleaneddata['''Mother's mean age at first birth'''].astype('float')

# Cleaning / Preprocessing for Maternal Mortality Ratio per 100,000 births Data
cleaneddata['Maternal mortality ratio'] = cleaneddata['Maternal mortality ratio'].str.split().str[0].str.replace(',','')
cleaneddata['Maternal mortality ratio'] = cleaneddata['Maternal mortality ratio'].astype('float')/100000

# Cleaning / Preprocessing for Infant Mortality Rate per 1000 births Data
cleaneddata['Infant mortality rate'] = cleaneddata['Infant mortality rate'].str.replace('\(\d{4}','', regex = True)
cleaneddata['Infant mortality rate'] = cleaneddata['Infant mortality rate'].str.split().str[1]
cleaneddata['Infant mortality rate'] = cleaneddata['Infant mortality rate'].str.replace('[^0-9\.]','0',regex = True)
cleaneddata['Infant mortality rate'] = cleaneddata['Infant mortality rate'].astype('float')/1000

# Cleaning / Preprocessing for Life Expectancy Data
cleaneddata['Life expectancy at birth'] = cleaneddata['Life expectancy at birth'].str.split().str[2]
cleaneddata['Life expectancy at birth'] = cleaneddata['Life expectancy at birth'].str.replace('[^0-9\.]','0',regex = True)
cleaneddata['Life expectancy at birth'] = cleaneddata['Life expectancy at birth'].astype('float')

# Cleaning / Preprocessing for Fertility Rate Data
cleaneddata['Total fertility rate'] = cleaneddata['Total fertility rate'].str.replace('\(\d{4}','', regex = True)
cleaneddata['Total fertility rate'] = cleaneddata['Total fertility rate'].str.split().str[0]
cleaneddata['Total fertility rate'] = cleaneddata['Total fertility rate'].str.replace('[^0-9\.]', '0', regex = True)
cleaneddata['Total fertility rate'] = cleaneddata['Total fertility rate'].astype('float')

# Cleaning / Preprocessing for Contraceptive Prevalence Rate Data
cleaneddata['Contraceptive prevalence rate'] = cleaneddata['Contraceptive prevalence rate'].str.split('%').str[0]
cleaneddata['Contraceptive prevalence rate'] = cleaneddata['Contraceptive prevalence rate'].replace('NA',np.nan)
cleaneddata['Contraceptive prevalence rate'] = cleaneddata['Contraceptive prevalence rate'].astype('float')

# Cleaning / Preprocessing for Current Healthcare Expenditure Rate Data
cleaneddata['Current health expenditure'] = cleaneddata['Current health expenditure'].str.split('%').str[0]
cleaneddata['Current health expenditure'] = cleaneddata['Current health expenditure'].replace('NA', np.nan)
cleaneddata['Current health expenditure'] = cleaneddata['Current health expenditure'].astype('float')
cleaneddata = cleaneddata.rename(columns = {'Current health expenditure' : 'Current health expenditure (%)'})

# Cleaning / Preprocessing for Physicians Density Data per 1000
cleaneddata['Physicians density'] = cleaneddata['Physicians density'].str.split().str[0]
cleaneddata['Physicians density'] = cleaneddata['Physicians density'].replace('NA', np.nan)
cleaneddata['Physicians density'] = cleaneddata['Physicians density'].astype('float')/1000

# Cleaning / Preprocessing for Hospital Bed Density Data per 1000
cleaneddata['Hospital bed density'] = cleaneddata['Hospital bed density'].str.split().str[0]
cleaneddata['Hospital bed density'] = cleaneddata['Hospital bed density'].astype('float')/1000

# Cleaning / Preprocessing for Obesity Rate Data
cleaneddata = cleaneddata.rename(columns = {'Obesity - adult prevalence rate' : 'Obesity - adult prevalence rate (%)'})
cleaneddata['Obesity - adult prevalence rate (%)'] = cleaneddata['Obesity - adult prevalence rate (%)'].str.split('%').str[0].astype('float')

# Cleaning / Preprocessing for Alcohol Consumption Rate Data
cleaneddata['Alcohol consumption per capita']= cleaneddata['Alcohol consumption per capita'].str.split().str[1].astype('float')

# Cleaning / Preprocessing for Tobacco use Data
cleaneddata = cleaneddata.rename(columns = {'Tobacco use' : 'Tobacco use (%)'})
cleaneddata['Tobacco use (%)'] = cleaneddata['Tobacco use (%)'].str.split().str[1].str.replace('%', '').astype('float')

# Cleaning / Preprocessing for Underweight Children Data
cleaneddata = cleaneddata.rename(
    columns = {'Children under the age of 5 years underweight' : 'Children under the age of 5 years underweight (%)'})
cleaneddata['Children under the age of 5 years underweight (%)'] = cleaneddata['Children under the age of 5 years underweight (%)'].str.split('%').str[0]
cleaneddata['Children under the age of 5 years underweight (%)'] = cleaneddata['Children under the age of 5 years underweight (%)'].replace('NA', np.nan)
cleaneddata['Children under the age of 5 years underweight (%)'] = cleaneddata['Children under the age of 5 years underweight (%)'].astype('float')

# Cleaning / Preprocessing for Married Women Data
cleaneddata = cleaneddata.rename(columns = {'Currently married women (ages 15-49)' :'Currently married women (ages 15-49) (%)'})
cleaneddata['Currently married women (ages 15-49) (%)'] = cleaneddata['Currently married women (ages 15-49) (%)'].str.split('%').str[0].astype('float')

# Cleaning / Preprocessing for Education Expenditure Data
cleaneddata['Education expenditures'] = cleaneddata['Education expenditures'].str.split('%').str[0].replace('NA', np.nan).astype('float')

# Cleaning / Preprocessing for Literacy Data
cleaneddata['Literacy'] = cleaneddata['Literacy'].str.replace('^.*lation: ', '', regex = True)
cleaneddata['Literacy'] = cleaneddata['Literacy'].str.split('%').str[0].replace('[^0-9\.]', '0', regex = True).astype('float')
cleaneddata['Literacy'] = cleaneddata['Literacy'].replace(0, np.nan)

# Cleaning / Preprocessing for School Life Expectancy Data
cleaneddata['School life expectancy (primary to tertiary education)'] = cleaneddata['School life expectancy (primary to tertiary education)'].str.split().str[1].astype('float')

# Cleaning / Preprocessing for Youth Unemployment Rate Data
cleaneddata['Youth unemployment rate (ages 15-24)'] = cleaneddata['Youth unemployment rate (ages 15-24)'].str.split('%').str[0]
cleaneddata['Youth unemployment rate (ages 15-24)'] = cleaneddata['Youth unemployment rate (ages 15-24)'].str.split().str[1].astype('float')

# Cleaning / Preprocessing for Youth Unemployment Rate Data
cleaneddata['Revenue from forest resources'] = cleaneddata['Revenue from forest resources'].str.split('%').str[0].astype('float')
cleaneddata = cleaneddata.rename(columns = {'Revenue from forest resources':'Revenue from forest resources (% of GDP)'})

# Cleaning / Preprocessing for Revenue From Coal Data
cleaneddata = cleaneddata.rename(columns = {'Revenue from coal':'Revenue from coal (% of GDP)'})
cleaneddata['Revenue from coal (% of GDP)'] = cleaneddata['Revenue from coal (% of GDP)'].str.split('%').str[0].astype('float')

# Cleaning / Preprocessing for Waste and Recycling Data in tons
cleaneddata['Waste and recycling'] = cleaneddata['Waste and recycling'].str.replace('municipal solid waste generated annually: ','')
cleaneddata['Waste and recycling'] = cleaneddata['Waste and recycling'].str.split('tons').str[0]
cleaneddata['million'] = cleaneddata['Waste and recycling'].str.replace('[^A-Za-z]','', regex = True)
cleaneddata['million'] = cleaneddata['million'].replace('', np.nan).fillna('1').str.replace('million', '1000000').astype('float')
cleaneddata['Waste and recycling'] = cleaneddata['Waste and recycling'].str.replace('[^0-9\.]','',regex = True)
cleaneddata['Waste and recycling'] = cleaneddata['Waste and recycling'].astype('float')
cleaneddata['Waste and recycling'] = cleaneddata['Waste and recycling']*cleaneddata['million']
cleaneddata = cleaneddata.rename(columns = {'Waste and recycling' : 'Waste and recycling (tons)'})

# Cleaning / Preprocessing for Renewable Water Resources in cubic meters
cleaneddata['Total renewable water resources'] = cleaneddata['Total renewable water resources'].str.split('cubic').str[0]
cleaneddata['WaterMetric'] = cleaneddata['Total renewable water resources'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['WaterMetric'] = cleaneddata['WaterMetric'].str.replace('million', '1000000')
cleaneddata['WaterMetric'] = cleaneddata['WaterMetric'].str.replace('billion', '1000000000')
cleaneddata['WaterMetric'] = cleaneddata['WaterMetric'].str.replace('trillion', '1000000000000')
cleaneddata['WaterMetric'] = cleaneddata['WaterMetric'].replace('', np.nan)
cleaneddata['WaterMetric'] = cleaneddata['WaterMetric'].replace('NA', np.nan)
cleaneddata['WaterMetric'] = cleaneddata['WaterMetric'].fillna('1').astype('float')
cleaneddata['Total renewable water resources'] = cleaneddata['Total renewable water resources'].str.split().str[0]
cleaneddata['Total renewable water resources'] = cleaneddata['Total renewable water resources'].replace('NA', np.nan).astype('float')
cleaneddata['Total renewable water resources'] = cleaneddata['Total renewable water resources']*cleaneddata['WaterMetric']
cleaneddata = cleaneddata.rename(columns = {'Total renewable water resources':'Total renewable water resources (cubic meters)'})

# Cleaning / Preprocessing for Capital Data
cleaneddata['Capital'] = cleaneddata['Capital'].str.replace('geographic.*$','',regex = True)

# Cleaning / Preprocessing for Real GDP Data
cleaneddata['Real GDP (purchasing power parity)'] = cleaneddata['Real GDP (purchasing power parity)'].str.split(' \(').str[0]
cleaneddata['MoneyMetric'] = cleaneddata['Real GDP (purchasing power parity)'].str.split().str[1]
cleaneddata['MoneyMetric'] = cleaneddata['MoneyMetric'].str.replace('million', '1000000')
cleaneddata['MoneyMetric'] = cleaneddata['MoneyMetric'].str.replace('billion', '1000000000')
cleaneddata['MoneyMetric'] = cleaneddata['MoneyMetric'].str.replace('trillion', '1000000000000')
cleaneddata['MoneyMetric'] = cleaneddata['MoneyMetric'].fillna('1').astype('float')
cleaneddata['Real GDP (purchasing power parity)'] = cleaneddata['Real GDP (purchasing power parity)'].str.replace('[^0-9\.]','',regex = True)
cleaneddata['Real GDP (purchasing power parity)'] = cleaneddata['Real GDP (purchasing power parity)'].replace('', np.nan).astype('float')
cleaneddata['Real GDP (purchasing power parity)'] = cleaneddata['Real GDP (purchasing power parity)']*cleaneddata['MoneyMetric']

# Cleaning / Preprocessing for Real GDP Growth Rate Data
cleaneddata['Real GDP growth rate'] = cleaneddata['Real GDP growth rate'].str.split('%').str[0]
cleaneddata['Real GDP growth rate'] = cleaneddata['Real GDP growth rate'].replace('NA', np.nan).astype('float')

# Cleaning / Preprocessing for Real GDP Per Capita Data
cleaneddata['Real GDP per capita'] = cleaneddata['Real GDP per capita'].str.split().str[0]
cleaneddata['Real GDP per capita'] = cleaneddata['Real GDP per capita'].str.replace('[^0-9]','',regex = True).astype('float')

# Cleaning / Preprocessing for GDP by Exchange Rate Data
cleaneddata['GDP (official exchange rate)'] = cleaneddata['GDP (official exchange rate)'].str.split(' \(').str[0]
cleaneddata['GDPMetric'] = cleaneddata['GDP (official exchange rate)'].str.split().str[1]
cleaneddata['GDPMetric'] = cleaneddata['GDPMetric'].str.replace('million', '1000000')
cleaneddata['GDPMetric'] = cleaneddata['GDPMetric'].str.replace('billion', '1000000000')
cleaneddata['GDPMetric'] = cleaneddata['GDPMetric'].str.replace('trillion', '1000000000000')
cleaneddata['GDPMetric'] = cleaneddata['GDPMetric'].fillna('1').astype('float')
cleaneddata['GDP (official exchange rate)'] = cleaneddata['GDP (official exchange rate)'].str.replace('[^0-9\.]','',regex = True)
cleaneddata['GDP (official exchange rate)'] = cleaneddata['GDP (official exchange rate)'].replace('', np.nan).astype('float')
cleaneddata['GDP (official exchange rate)'] = cleaneddata['GDP (official exchange rate)']*cleaneddata['GDPMetric']

# Cleaning / Preprocessing for Inflation Rate Data
cleaneddata['Inflation rate (consumer prices)'] = cleaneddata['Inflation rate (consumer prices)'].str.split('%').str[0]
cleaneddata['Inflation rate (consumer prices)'] = cleaneddata['Inflation rate (consumer prices)'].str.replace('[^0-9\.\-]','',regex = True)
cleaneddata['Inflation rate (consumer prices)'] = cleaneddata['Inflation rate (consumer prices)'].replace('', np.nan).astype('float')

# Cleaning / Preprocessing for Industrial Production Growth Rate Data
cleaneddata['Industrial production growth rate'] = cleaneddata['Industrial production growth rate'].str.split('%').str[0]
cleaneddata['Industrial production growth rate'] = cleaneddata['Industrial production growth rate'].replace('NA', np.nan).astype('float')

# Cleaning / Preprocessing for Labor Force Data
cleaneddata['Labor force'] = cleaneddata['Labor force'].str.split(' \(').str[0]
cleaneddata['LaborMetric'] = cleaneddata['Labor force'].str.replace('[^A-Za-z]','', regex = True)
cleaneddata['LaborMetric'] = cleaneddata['LaborMetric'].replace('', np.nan)
cleaneddata['LaborMetric'] = cleaneddata['LaborMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['LaborMetric'] = cleaneddata['LaborMetric'].str.replace('million', '1000000').astype('float')
cleaneddata['Labor force'] = cleaneddata['Labor force'].str.replace('[^0-9\.]','',regex = True)
cleaneddata['Labor force'] = cleaneddata['Labor force'].replace('', np.nan).astype('float')
cleaneddata['Labor force'] = cleaneddata['Labor force']*cleaneddata['LaborMetric']

# Cleaning / Preprocessing for Unemployment Rate Data
cleaneddata['Unemployment rate'] = cleaneddata['Unemployment rate'].str.split('%').str[0]
cleaneddata['Unemployment rate'] = cleaneddata['Unemployment rate'].replace('NA', np.nan).astype('float')

# Cleaning / Preprocessing for Poverty Data
cleaneddata['Population below poverty line'] = cleaneddata['Population below poverty line'].str.split('%').str[0]
cleaneddata['Population below poverty line'] = cleaneddata['Population below poverty line'].str.replace('[^0-9\.]','',regex = True)
cleaneddata['Population below poverty line'] = cleaneddata['Population below poverty line'].replace('', np.nan).astype('float')

# Cleaning / Preprocessing for Gini Index Data
cleaneddata['Gini Index coefficient - distribution of family income'] = cleaneddata['Gini Index coefficient - distribution of family income'].str.split().str[0].astype('float')

# Cleaning / Preprocessing for Budget Data
cleaneddata['Budget'] = cleaneddata['Budget'].str.split('$').str[1]
cleaneddata['Budget'] = cleaneddata['Budget'].str.split(' \(').str[0]
cleaneddata['BudgetMetric'] = cleaneddata['Budget'].str.split().str[1]
cleaneddata['BudgetMetric'] = cleaneddata['BudgetMetric'].fillna('1')
cleaneddata['BudgetMetric'] = cleaneddata['BudgetMetric'].str.replace('million', '1000000')
cleaneddata['BudgetMetric'] = cleaneddata['BudgetMetric'].str.replace('billion', '1000000000')
cleaneddata['BudgetMetric'] = cleaneddata['BudgetMetric'].str.replace('trillion', '1000000000000').astype('float')
cleaneddata['Budget'] = cleaneddata['Budget'].str.replace('[^0-9\.]','', regex = True).astype('float')
cleaneddata['Budget'] = cleaneddata['Budget']*cleaneddata['BudgetMetric']

# Cleaning / Preprocessing for Budget Surplus/Deficit Data
cleaneddata['Budget surplus (+) or deficit (-)'] = cleaneddata['Budget surplus (+) or deficit (-)'].str.split('%').str[0]
cleaneddata['Budget surplus (+) or deficit (-)'] = cleaneddata['Budget surplus (+) or deficit (-)'].replace('NA', np.nan).astype('float')

# Cleaning / Preprocessing for Public Debt Data
cleaneddata['Public debt'] = cleaneddata['Public debt'].str.split('%').str[0].astype('float')
cleaneddata = cleaneddata.rename(columns = {'Public debt' : 'Public debt (% of GDP)'})

# Cleaning / Preprocessing for Taxes and Other Revenues Data
cleaneddata['Taxes and other revenues'] = cleaneddata['Taxes and other revenues'].str.split('%').str[0]
cleaneddata['Taxes and other revenues'] = cleaneddata['Taxes and other revenues'].replace('NA', np.nan).astype('float')

# Cleaning / Preprocessing for Current Account Balance Data
cleaneddata['Current account balance'] = cleaneddata['Current account balance'].str.split(' \(').str[0]
cleaneddata['balanceMetric'] = cleaneddata['Current account balance'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['balanceMetric'] = cleaneddata['balanceMetric'].replace('', np.nan).fillna('1')
cleaneddata['balanceMetric'] = cleaneddata['balanceMetric'].replace('million', '1000000')
cleaneddata['balanceMetric'] = cleaneddata['balanceMetric'].replace('billion', '1000000000').astype('float')
cleaneddata['Current account balance'] = cleaneddata['Current account balance'].str.replace('[^0-9\.\-]','', regex = True).astype('float')
cleaneddata['Current account balance'] = cleaneddata['Current account balance']*cleaneddata['balanceMetric']

# Cleaning / Preprocessing for Exports Data
cleaneddata['Exports'] = cleaneddata['Exports'].str.split(' \(').str[0]
cleaneddata['ExportsMetric'] = cleaneddata['Exports'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['ExportsMetric'] = cleaneddata['ExportsMetric'].replace('', np.nan)
cleaneddata['ExportsMetric'] = cleaneddata['ExportsMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['ExportsMetric'] = cleaneddata['ExportsMetric'].replace('million', '1000000')
cleaneddata['ExportsMetric'] = cleaneddata['ExportsMetric'].replace('billion', '1000000000')
cleaneddata['ExportsMetric'] = cleaneddata['ExportsMetric'].replace('trillion', '1000000000000').astype('float')
cleaneddata['Exports'] = cleaneddata['Exports'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Exports'] = cleaneddata['Exports'].replace('', np.nan).astype('float')
cleaneddata['Exports'] = cleaneddata['Exports']*cleaneddata['ExportsMetric']

# Cleaning / Preprocessing for Imports Data
cleaneddata['Imports'] = cleaneddata['Imports'].str.split(' \(').str[0]
cleaneddata['ImportsMetric'] = cleaneddata['Imports'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['ImportsMetric'] = cleaneddata['ImportsMetric'].replace('', np.nan)
cleaneddata['ImportsMetric'] = cleaneddata['ImportsMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['ImportsMetric'] = cleaneddata['ImportsMetric'].replace('million', '1000000')
cleaneddata['ImportsMetric'] = cleaneddata['ImportsMetric'].replace('billion', '1000000000')
cleaneddata['ImportsMetric'] = cleaneddata['ImportsMetric'].replace('trillion', '1000000000000').astype('float')
cleaneddata['Imports'] = cleaneddata['Imports'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Imports'] = cleaneddata['Imports'].replace('', np.nan).astype('float')
cleaneddata['Imports'] = cleaneddata['Imports']*cleaneddata['ImportsMetric']

# Cleaning / Preprocessing for Foreign Reserves Data
cleaneddata['Reserves of foreign exchange and gold'] = cleaneddata['Reserves of foreign exchange and gold'].str.split(' \(').str[0]
cleaneddata['goldMetric'] = cleaneddata['Reserves of foreign exchange and gold'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['goldMetric'] = cleaneddata['goldMetric'].replace('', np.nan)
cleaneddata['goldMetric'] = cleaneddata['goldMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['goldMetric'] = cleaneddata['goldMetric'].replace('million', '1000000')
cleaneddata['goldMetric'] = cleaneddata['goldMetric'].replace('billion', '1000000000')
cleaneddata['goldMetric'] = cleaneddata['goldMetric'].replace('trillion', '1000000000000').astype('float')
cleaneddata['Reserves of foreign exchange and gold'] = cleaneddata['Reserves of foreign exchange and gold'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Reserves of foreign exchange and gold'] = cleaneddata['Reserves of foreign exchange and gold'].replace('', np.nan).astype('float')
cleaneddata['Reserves of foreign exchange and gold'] = cleaneddata['Reserves of foreign exchange and gold']*cleaneddata['goldMetric']

# Cleaning / Preprocessing for Debt - external Data
cleaneddata['Debt - external'] = cleaneddata['Debt - external'].str.split(' \(').str[0]
cleaneddata['DebtMetric'] = cleaneddata['Debt - external'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['DebtMetric'] = cleaneddata['DebtMetric'].replace('', np.nan)
cleaneddata['DebtMetric'] = cleaneddata['DebtMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['DebtMetric'] = cleaneddata['DebtMetric'].replace('million', '1000000')
cleaneddata['DebtMetric'] = cleaneddata['DebtMetric'].replace('billion', '1000000000')
cleaneddata['DebtMetric'] = cleaneddata['DebtMetric'].replace('trillion', '1000000000000')
cleaneddata['DebtMetric'] = cleaneddata['DebtMetric'].replace('[A-Za-z]', np.nan, regex = True).fillna('1').astype('float')
cleaneddata['Debt - external'] = cleaneddata['Debt - external'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Debt - external'] = cleaneddata['Debt - external'].replace('', np.nan).astype('float')
cleaneddata['Debt - external'] = cleaneddata['Debt - external']*cleaneddata['DebtMetric']

# Cleaning / Preprocessing for Electricity Access Data
cleaneddata['Electricity access'] = cleaneddata['Electricity access'].str.split('%').str[0]
cleaneddata['Electricity access'] = cleaneddata['Electricity access'].str.split('n: ').str[1]#.str.replace('[^0-9\.]','',regex = True)
cleaneddata['Electricity access'] = cleaneddata['Electricity access'].astype('float')

# Cleaning / Preprocessing for Electricity Data
cleaneddata['Electricity'] = cleaneddata['Electricity'].str.replace('^.*capacity: ','',regex = True)
cleaneddata['Electricity'] = cleaneddata['Electricity'].str.split(' kW').str[0]
cleaneddata['ElectricityMetric'] = cleaneddata['Electricity'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['ElectricityMetric'] = cleaneddata['ElectricityMetric'].replace('', np.nan)
cleaneddata['ElectricityMetric'] = cleaneddata['ElectricityMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['ElectricityMetric'] = cleaneddata['ElectricityMetric'].replace('million', '1000000').astype('float')
cleaneddata['Electricity'] = cleaneddata['Electricity'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Electricity'] = cleaneddata['Electricity'].replace('', np.nan).astype('float')
cleaneddata['Electricity'] = cleaneddata['Electricity']*cleaneddata['ElectricityMetric']
cleaneddata = cleaneddata.rename(columns={'Electricity' : 'Electricity (kW)'})

# Cleaning / Preprocessing for Coal Data
cleaneddata['Coal'] = cleaneddata['Coal'].str.split(' metric').str[0]
cleaneddata['Coal'] = cleaneddata['Coal'].str.split(': ').str[1]
cleaneddata['CoalMetric'] = cleaneddata['Coal'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['CoalMetric'] = cleaneddata['CoalMetric'].replace('', np.nan)
cleaneddata['CoalMetric'] = cleaneddata['CoalMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['CoalMetric'] = cleaneddata['CoalMetric'].replace('million', '1000000').astype('float')
cleaneddata['Coal'] = cleaneddata['Coal'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Coal'] = cleaneddata['Coal'].replace('', np.nan).astype('float')
cleaneddata['Coal'] = cleaneddata['Coal']*cleaneddata['CoalMetric']
cleaneddata = cleaneddata.rename(columns={'Coal' : 'Coal (tons)'})

# Cleaning / Preprocessing for Petroleum Data
cleaneddata['Petroleum'] = cleaneddata['Petroleum'].str.split(' bbl').str[0]
cleaneddata['Petroleum'] = cleaneddata['Petroleum'].str.split(': ').str[1]
cleaneddata['PetroleumMetric'] = cleaneddata['Petroleum'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['PetroleumMetric'] = cleaneddata['PetroleumMetric'].replace('', np.nan)
cleaneddata['PetroleumMetric'] = cleaneddata['PetroleumMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['PetroleumMetric'] = cleaneddata['PetroleumMetric'].replace('million', '1000000').astype('float')
cleaneddata['Petroleum'] = cleaneddata['Petroleum'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Petroleum'] = cleaneddata['Petroleum'].replace('', np.nan).astype('float')
cleaneddata['Petroleum'] = cleaneddata['Petroleum']*cleaneddata['PetroleumMetric']
cleaneddata = cleaneddata.rename(columns={'Petroleum' : 'Petroleum (bbl/day)'})

# Cleaning / Preprocessing for Refined Petroleum Production Data
cleaneddata['Refined petroleum products - production'] = cleaneddata['Refined petroleum products - production'].str.split(' bbl').str[0]
cleaneddata['productionMetric'] = cleaneddata['Refined petroleum products - production'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['productionMetric'] = cleaneddata['productionMetric'].replace('', np.nan)
cleaneddata['productionMetric'] = cleaneddata['productionMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['productionMetric'] = cleaneddata['productionMetric'].str.replace('million', '1000000').astype('float')
cleaneddata['Refined petroleum products - production'] = cleaneddata['Refined petroleum products - production'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Refined petroleum products - production'] = cleaneddata['Refined petroleum products - production'].replace('', np.nan).astype('float')
cleaneddata['Refined petroleum products - production'] = cleaneddata['Refined petroleum products - production']*cleaneddata['productionMetric']

# Cleaning / Preprocessing for Refined Petroleum Production exports Data
cleaneddata['Refined petroleum products - exports'] = cleaneddata['Refined petroleum products - exports'].str.split(' bbl').str[0]
cleaneddata['exportMetric'] = cleaneddata['Refined petroleum products - exports'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['exportMetric'] = cleaneddata['exportMetric'].replace('', np.nan)
cleaneddata['exportMetric'] = cleaneddata['exportMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['exportMetric'] = cleaneddata['exportMetric'].str.replace('million', '1000000').astype('float')
cleaneddata['Refined petroleum products - exports'] = cleaneddata['Refined petroleum products - exports'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Refined petroleum products - exports'] = cleaneddata['Refined petroleum products - exports'].replace('', np.nan).astype('float')
cleaneddata['Refined petroleum products - exports'] = cleaneddata['Refined petroleum products - exports']*cleaneddata['exportMetric']

# Cleaning / Preprocessing for Refined Petroleum Production imports Data
cleaneddata['Refined petroleum products - imports'] = cleaneddata['Refined petroleum products - imports'].str.split(' bbl').str[0]
cleaneddata['importMetric'] = cleaneddata['Refined petroleum products - imports'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['importMetric'] = cleaneddata['importMetric'].replace('', np.nan)
cleaneddata['importMetric'] = cleaneddata['importMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['importMetric'] = cleaneddata['importMetric'].str.replace('million', '1000000').astype('float')
cleaneddata['Refined petroleum products - imports'] = cleaneddata['Refined petroleum products - imports'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Refined petroleum products - imports'] = cleaneddata['Refined petroleum products - imports'].replace('', np.nan).astype('float')
cleaneddata['Refined petroleum products - imports'] = cleaneddata['Refined petroleum products - imports']*cleaneddata['importMetric']

# Cleaning / Preprocessing for Natural Gas Data
cleaneddata['Natural gas'] = cleaneddata['Natural gas'].str.split(' cubic').str[0]
cleaneddata['Natural gas'] = cleaneddata['Natural gas'].str.split(': ').str[1]
cleaneddata['NaturalMetric'] = cleaneddata['Natural gas'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['NaturalMetric'] = cleaneddata['NaturalMetric'].replace('', np.nan)
cleaneddata['NaturalMetric'] = cleaneddata['NaturalMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['NaturalMetric'] = cleaneddata['NaturalMetric'].str.replace('million', '1000000')
cleaneddata['NaturalMetric'] = cleaneddata['NaturalMetric'].str.replace('billion', '1000000000').astype('float')
cleaneddata['Natural gas'] = cleaneddata['Natural gas'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Natural gas'] = cleaneddata['Natural gas'].replace('', np.nan).astype('float')
cleaneddata['Natural gas'] = cleaneddata['Natural gas']*cleaneddata['NaturalMetric']
cleaneddata = cleaneddata.rename(columns={'Natural gas' : 'Natural gas (cubic meters)'})

# Cleaning / Preprocessing for Carbon Dioxide Emissions Data
cleaneddata['Carbon dioxide emissions'] = cleaneddata['Carbon dioxide emissions'].str.split(' metric').str[0]
cleaneddata['CarbonMetric'] = cleaneddata['Carbon dioxide emissions'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['CarbonMetric'] = cleaneddata['CarbonMetric'].replace('', np.nan)
cleaneddata['CarbonMetric'] = cleaneddata['CarbonMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['CarbonMetric'] = cleaneddata['CarbonMetric'].str.replace('million', '1000000').astype('float')
cleaneddata['Carbon dioxide emissions'] = cleaneddata['Carbon dioxide emissions'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Carbon dioxide emissions'] = cleaneddata['Carbon dioxide emissions'].replace('', np.nan).astype('float')
cleaneddata['Carbon dioxide emissions'] = cleaneddata['Carbon dioxide emissions']*cleaneddata['CarbonMetric']
cleaneddata = cleaneddata.rename(columns={'Carbon dioxide emissions' : 'Carbon dioxide emissions (metric tons)'})

# Cleaning / Preprocessing for Energy Consumption Per Capita Data
cleaneddata['Energy consumption per capita'] = cleaneddata['Energy consumption per capita'].str.split(' Btu').str[0]
cleaneddata['capitaMetric'] = cleaneddata['Energy consumption per capita'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['capitaMetric'] = cleaneddata['capitaMetric'].replace('', np.nan)
cleaneddata['capitaMetric'] = cleaneddata['capitaMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['capitaMetric'] = cleaneddata['capitaMetric'].str.replace('million', '1000000').astype('float')
cleaneddata['Energy consumption per capita'] = cleaneddata['Energy consumption per capita'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Energy consumption per capita'] = cleaneddata['Energy consumption per capita'].replace('', np.nan).astype('float')
cleaneddata['Energy consumption per capita'] = cleaneddata['Energy consumption per capita']*cleaneddata['capitaMetric']
cleaneddata = cleaneddata.rename(columns={'Energy consumption per capita' : 'Energy consumption per capita (Btu/person)'})

# Cleaning / Preprocessing for Telephones Data
cleaneddata['Telephones - fixed lines'] = cleaneddata['Telephones - fixed lines'].str.split(' \(').str[0]
cleaneddata['Telephones - fixed lines'] = cleaneddata['Telephones - fixed lines'].str.split(': ').str[1]
cleaneddata['TelephonesMetric'] = cleaneddata['Telephones - fixed lines'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['TelephonesMetric'] = cleaneddata['TelephonesMetric'].replace('', np.nan)
cleaneddata['TelephonesMetric'] = cleaneddata['TelephonesMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['TelephonesMetric'] = cleaneddata['TelephonesMetric'].str.replace('million', '1000000').astype('float')
cleaneddata['Telephones - fixed lines'] = cleaneddata['Telephones - fixed lines'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Telephones - fixed lines'] = cleaneddata['Telephones - fixed lines'].replace('', np.nan).astype('float')
cleaneddata['Telephones - fixed lines'] = cleaneddata['Telephones - fixed lines']*cleaneddata['TelephonesMetric']

# Cleaning / Preprocessing for Wireless Phones Data
cleaneddata['Telephones - mobile cellular'] = cleaneddata['Telephones - mobile cellular'].str.split(' \(').str[0]
cleaneddata['Telephones - mobile cellular'] = cleaneddata['Telephones - mobile cellular'].str.split(': ').str[1]
cleaneddata['cellularMetric'] = cleaneddata['Telephones - mobile cellular'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['cellularMetric'] = cleaneddata['cellularMetric'].replace('', np.nan)
cleaneddata['cellularMetric'] = cleaneddata['cellularMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['cellularMetric'] = cleaneddata['cellularMetric'].str.replace('million', '1000000')
cleaneddata['cellularMetric'] = cleaneddata['cellularMetric'].str.replace('billion', '1000000000').astype('float')
cleaneddata['Telephones - mobile cellular'] = cleaneddata['Telephones - mobile cellular'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Telephones - mobile cellular'] = cleaneddata['Telephones - mobile cellular'].replace('', np.nan).astype('float')
cleaneddata['Telephones - mobile cellular'] = cleaneddata['Telephones - mobile cellular']*cleaneddata['cellularMetric']


# Cleaning / Preprocessing for Internet Users Data
cleaneddata['Internet users'] = cleaneddata['Internet users'].str.split(' \(').str[0]
cleaneddata['Internet users'] = cleaneddata['Internet users'].str.split(': ').str[1]
cleaneddata['InternetMetric'] = cleaneddata['Internet users'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['InternetMetric'] = cleaneddata['InternetMetric'].replace('', np.nan)
cleaneddata['InternetMetric'] = cleaneddata['InternetMetric'].replace('NA', np.nan).fillna('1')
cleaneddata['InternetMetric'] = cleaneddata['InternetMetric'].str.replace('million', '1000000')
cleaneddata['InternetMetric'] = cleaneddata['InternetMetric'].str.replace('billion', '1000000000').astype('float')
cleaneddata['Internet users'] = cleaneddata['Internet users'].str.replace('[^0-9\.\-]','', regex = True)
cleaneddata['Internet users'] = cleaneddata['Internet users'].replace('', np.nan).astype('float')
cleaneddata['Internet users'] = cleaneddata['Internet users']*cleaneddata['InternetMetric']

# Cleaning / Preprocessing for National Air Transport System Data
cleaneddata['Airports'] = cleaneddata['Airports'].str.split().str[0].str.replace(',','').astype('float')

# Cleaning / Preprocessing for Railways Data
cleaneddata['Railways'] = cleaneddata['Railways'].str.split(' km').str[0].str.replace('[^0-9\.\-]','', regex = True).replace('', np.nan).astype('float')
cleaneddata = cleaneddata.rename(columns={'Railways' : 'Railways (km)'})

# Cleaning / Preprocessing for Roadways Data
cleaneddata['Roadways'] = cleaneddata['Roadways'].str.split(' km').str[0].str.split(': ').str[1]
cleaneddata['RoadwaysMetric'] = cleaneddata['Roadways'].str.replace('[^A-Za-z]', '', regex = True)
cleaneddata['RoadwaysMetric'] = cleaneddata['RoadwaysMetric'].replace('', np.nan)
cleaneddata['RoadwaysMetric'] = cleaneddata['RoadwaysMetric'].replace('NA', np.nan)
cleaneddata['RoadwaysMetric'] = cleaneddata['RoadwaysMetric'].str.replace('million', '1000000')
cleaneddata['RoadwaysMetric'] = cleaneddata['RoadwaysMetric'].str.replace('[^0-9\.\-]','', regex = True).replace('', np.nan).replace('', np.nan).fillna(1).astype('float')
cleaneddata['Roadways'] = cleaneddata['Roadways'].str.split().str[0].str.replace('[^0-9\.\-]','', regex = True).replace('', np.nan).astype('float')*cleaneddata['RoadwaysMetric']

cleaneddata = cleaneddata.rename(columns={'Roadways' : 'Roadways (km)'})

# Cleaning / Preprocessing for Waterways Data
cleaneddata['Waterways'] = cleaneddata['Waterways'].str.split(' km').str[0]
cleaneddata['Waterways'] = cleaneddata['Waterways'].str.replace('^\(.*\)','',regex = True).str.replace('[^0-9\.\-]','', regex = True).replace('', np.nan).astype('float')
cleaneddata = cleaneddata.rename(columns={'Waterways' : 'Waterways (km)'})

# Cleaning / Preprocessing for Military Expenditures Data
cleaneddata['Military expenditures'] = cleaneddata['Military expenditures'].str.split('%').str[0]
cleaneddata['Military expenditures'] = cleaneddata['Military expenditures'].str.replace('^\D.*\s','', regex = True)
cleaneddata['Military expenditures'] = cleaneddata['Military expenditures'].str.replace('\-.*','', regex = True).str.replace('[^0-9\.\-]','', regex = True).replace('', np.nan).astype('float')

cleaneddata = cleaneddata.rename(columns={'Military expenditures' : 'Military expenditures (% of GDP)'})

# Cleaning / Preprocessing for Refugees Data
cleaneddata['Heliports'] = cleaneddata['Heliports'].str.split().str[0].str.replace(',','').astype('float')


# Cleaning and processing for Country Names
cleaneddata['name'] = cleaneddata['name'].str.replace('-', ' ')
cleaneddata['name'] = cleaneddata['name'].str.title()
cleaneddata.loc[cleaneddata['name'].str.split().str[-1] == 'The', 'name'] = cleaneddata['name'] + ' ' + cleaneddata['name'].str.split().str[0]
cleaneddata.loc[cleaneddata['name'].str.split().str[-1] == 'Of', 'name'] = cleaneddata['name'] + ' ' + cleaneddata['name'].str.split().str[0]
cleaneddata.loc[cleaneddata['name'].str.split().str[-1] == cleaneddata['name'].str.split().str[0], 'name'] = cleaneddata['name'].str.replace('^\S*\s','',regex = True)
cleaneddata.loc[cleaneddata['name'].str.contains('Korea'), 'name'] = cleaneddata['name'].str.split().str[-1] + ' ' + cleaneddata['name'].str.split().str[0]
cleaneddata.loc[cleaneddata['name'].str.contains('Turkiye'), 'name'] = 'Turkey'
cleaneddata.loc[cleaneddata['name'].str.contains('Cote Divoire'), 'name'] = '''Cote d'Ivoire'''

# Adds Western Sahara country name for Tableau to recognize on the mapping visualization,
# though the US has officially recognized Western Sahara as a part of Morocco
# since 2020 (CIA World Factbook, 2023). My map visualization will recognize
# the former Western Sahara as contiguous with Moroccan borders
WesternSahara = cleaneddata[cleaneddata['name'] == 'Morocco']
WesternSahara['name'] = 'Western Sahara'
cleaneddata = pd.concat([cleaneddata, WesternSahara], sort=False)

# test = 'Population'
# print(cleaneddata[[test,'name']].to_string())
# # # #
# # #
# #
# print(cleaneddata[['name',test]].sort_values(by=test,ascending=False).to_string())


<timed exec>:39: FutureWarning: The default value of regex will change from True to False in a future version.
<timed exec>:42: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
<timed exec>:65: FutureWarning: The default value of regex will change from True to False in a future version.
<timed exec>:80: FutureWarning: The default value of regex will change from True to False in a future version.
<timed exec>:81: FutureWarning: The default value of regex will change from True to False in a future version.


CPU times: user 604 ms, sys: 3.05 ms, total: 607 ms
Wall time: 616 ms


<timed exec>:569: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [27]:
#Converts cleaned dataframe into a csv or Excel file, which can be used for Tableau visualizations

#cleaneddata.to_csv('cleanedWorldFactbookDataframe.csv')
cleaneddata.to_excel('cleanedWorldFactbookDataframe.xlsx')

In [ ]:
#@title
%%time
import requests
import pandas as pd
from bs4 import BeautifulSoup

# URL of the web page to scrape
url = 'https://www.cia.gov/the-world-factbook/countries/germany/'
print(url.split('/')[-2])
countriesname = url.split('/')[-2]
#url = 'https://en.wikipedia.org/wiki/Hip_hop_music'
#url = 'https://www.cia.gov/the-world-factbook/countries/'
# Send an HTTP GET request and retrieve the HTML content
response = requests.get(url)
html_content = response.content

# Create a BeautifulSoup object
soup = BeautifulSoup(html_content, 'html.parser')

# Find all headings and paragraphs
headings = soup.find_all(['h1', 'h2', 'h3', 'h4', 'h5', 'h6'])
paragraphs = soup.find_all('p')

# Create a mapping of heading to paragraph
heading_paragraph_map = {}

# Iterate over headings
for heading in headings:
    # Find the next paragraph sibling for each heading
    next_paragraph = heading.find_next_sibling('p')
    if next_paragraph:
        # Store the heading as the key and the paragraph text as the value
        heading_paragraph_map[heading.text.strip()] = next_paragraph.text.strip()

#Processes html headings and paragraphs into pandas dataframe
columns = ['name']
rows = [countriesname]
#Print the heading and corresponding paragraph
for heading, paragraph in heading_paragraph_map.items():
    #print('Heading:', heading)
    #print('Paragraph:', paragraph)
    columns.append(heading)
    rows.append(paragraph)
    #print()
print(columns)
print(rows)
print(heading_paragraph_map.items())

rawcountries = pd.DataFrame([rows], columns = columns)


# French Test BELOW
url = 'https://www.cia.gov/the-world-factbook/countries/france/'
print(url.split('/')[-2])
countriesname = url.split('/')[-2]
#url = 'https://en.wikipedia.org/wiki/Hip_hop_music'
#url = 'https://www.cia.gov/the-world-factbook/countries/'
# Send an HTTP GET request and retrieve the HTML content
response = requests.get(url)
html_content = response.content

# Create a BeautifulSoup object
soup = BeautifulSoup(html_content, 'html.parser')

# Find all headings and paragraphs
headings = soup.find_all(['h1', 'h2', 'h3', 'h4', 'h5', 'h6'])
paragraphs = soup.find_all('p')

# Create a mapping of heading to paragraph
heading_paragraph_map = {}

# Iterate over headings
for heading in headings:
    # Find the next paragraph sibling for each heading
    next_paragraph = heading.find_next_sibling('p')
    if next_paragraph:
        # Store the heading as the key and the paragraph text as the value
        heading_paragraph_map[heading.text.strip()] = next_paragraph.text.strip()

#Processes html headings and paragraphs into pandas dataframe
columns = ['name']
rows = [countriesname]
#Print the heading and corresponding paragraph
for heading, paragraph in heading_paragraph_map.items():
    #print('Heading:', heading)
    #print('Paragraph:', paragraph)
    columns.append(heading)
    rows.append(paragraph)
    #print()
print(columns)
print(rows)
print(heading_paragraph_map.items())

francetest = pd.DataFrame([rows], columns = columns)

print(rawcountries.dtypes.to_string())
print(rawcountries)
print(francetest)

rawcountries = pd.concat([rawcountries, francetest], sort=False)
print(rawcountries)

germany
['name', 'Background', 'Location', 'Geographic coordinates', 'Map references', 'Area', 'Area - comparative', 'Land boundaries', 'Coastline', 'Maritime claims', 'Climate', 'Terrain', 'Elevation', 'Natural resources', 'Land use', 'Irrigated land', 'Major lakes (area sq km)', 'Major rivers (by length in km)', 'Major watersheds (area sq km)', 'Population distribution', 'Natural hazards', 'Geography - note', 'Population', 'Nationality', 'Ethnic groups', 'Languages', 'Religions', 'Age structure', 'Dependency ratios', 'Median age', 'Population growth rate', 'Birth rate', 'Death rate', 'Net migration rate', 'Urbanization', 'Major urban areas - population', 'Sex ratio', "Mother's mean age at first birth", 'Maternal mortality ratio', 'Infant mortality rate', 'Life expectancy at birth', 'Total fertility rate', 'Gross reproduction rate', 'Contraceptive prevalence rate', 'Drinking water source', 'Current health expenditure', 'Physicians density', 'Hospital bed density', 'Sanitation facility

In [ ]:
#@title
import requests
from bs4 import BeautifulSoup
import pandas as pd

# URL of the Wikipedia article with the table
url = 'https://en.wikipedia.org/wiki/List_of_countries_by_population_(United_Nations)'

# Send an HTTP GET request and retrieve the HTML content
response = requests.get(url)
html_content = response.content

# Create a BeautifulSoup object
soup = BeautifulSoup(html_content, 'html.parser')

# Find all the tables
tables = soup.find_all('table')

# Extract data from the desired table (e.g., the first table)
desired_table = tables[0]

# Extract table headers
headers = []
header_row = desired_table.find('tr')
header_cells = header_row.find_all('th')
for cell in header_cells:
    headers.append(cell.text.strip())

# Extract table rows and cells
data = []
rows = desired_table.find_all('tr')[1:]  # Exclude the header row
for row in rows:
    cells = row.find_all('td')
    row_data = [cell.text.strip() for cell in cells]
    data.append(row_data)

# Create a pandas DataFrame from the extracted data
df = pd.DataFrame(data, columns=headers)

# Print the DataFrame
print(df)


#Preprocessing and cleaning
processing = df
processing['Population(1 July 2022)'] = processing['Population(1 July 2022)'].str.replace(',','')
processing['Population(1 July 2022)'] = processing['Population(1 July 2022)'].fillna('0')
processing['Population(1 July 2022)'] = processing['Population(1 July 2022)'].astype(int)
print(processing.sort_values(by = 'Population(1 July 2022)', ascending = False))
print(processing.dtypes)

                        Country / Area UN continentalregion[4]  \
0                                India                    Asia   
1                             China[a]                    Asia   
2                        United States                Americas   
3                            Indonesia                    Asia   
4                             Pakistan                    Asia   
..                                 ...                     ...   
232        Montserrat (United Kingdom)                Americas   
233  Falkland Islands (United Kingdom)                Americas   
234                               Niue                 Oceania   
235              Tokelau (New Zealand)                 Oceania   
236                               None                    None   

    UN statisticalsubregion[4] Population(1 July 2022)  \
0                Southern Asia           1,417,173,173   
1                 Eastern Asia           1,425,887,337   
2             Northern America   

In [ ]:
#@title
import requests
from bs4 import BeautifulSoup
import pandas as pd

# URL of the Wikipedia article with the table
url = 'https://en.wikipedia.org/wiki/List_of_presidents_of_the_United_States'

# Send an HTTP GET request and retrieve the HTML content
response = requests.get(url)
html_content = response.content

# Create a BeautifulSoup object
soup = BeautifulSoup(html_content, 'html.parser')

# Find all the tables
tables = soup.find_all('table')

# Extract data from the desired table (e.g., the first table)
desired_table = tables[0]

# Extract table headers
headers = []
header_row = desired_table.find('tr')
header_cells = header_row.find_all('th')
for cell in header_cells:
    headers.append(cell.text.strip())

# Extract table rows and cells
data = []
rows = desired_table.find_all('tr')[1:]  # Exclude the header row
for row in rows:
    cells = row.find_all('td')
    row_data = [cell.text.strip() for cell in cells]
    data.append(row_data)

# Create a pandas DataFrame from the extracted data
df = pd.DataFrame(data, columns=headers)

# Print the DataFrame
print(df)



   No.[a]                               Portrait  \
0               George Washington(1732–1799)[17]   
1                      John Adams(1735–1826)[19]   
2                Thomas Jefferson(1743–1826)[21]   
3                   James Madison(1751–1836)[22]   
4                    James Monroe(1758–1831)[24]   
5               John Quincy Adams(1767–1848)[25]   
6                  Andrew Jackson(1767–1845)[28]   
7                Martin Van Buren(1782–1862)[29]   
8          William Henry Harrison(1773–1841)[30]   
9                      John Tyler(1790–1862)[31]   
10                  James K. Polk(1795–1849)[34]   
11                 Zachary Taylor(1784–1850)[35]   
12               Millard Fillmore(1800–1874)[36]   
13                Franklin Pierce(1804–1869)[38]   
14                 James Buchanan(1791–1868)[39]   
15                Abraham Lincoln(1809–1865)[40]   
16                 Andrew Johnson(1808–1875)[42]   
17               Ulysses S. Grant(1822–1885)[43]   
18          

In [8]:
# test = """afghanistan/">Afghanistan</a></td><td>AFG</td><td>AF | AFG | 004</td><td>AFG</td><td>.af</td><td> - </td></tr><tr class="content-"""
# print(test[:test.index('/')])
import pandas as pd
df = pd.read_csv('cleanedWorldFactbookDataframe.csv')
#print(df.dtypes.to_string())
df.to_excel('cleanedWorldFactbookDataframe.xlsx')

In [15]:
# WesternSahara = cleaneddata[cleaneddata['name'] == 'Morocco']
# WesternSahara['name'] = 'Western Sahara'
# print(WesternSahara)